In [3]:
from sklearn import metrics
 
import gensim.models as g
import codecs
import pandas as pd
 
model="..\data\doc2vec\doc2vec.bin"
test_docs="..\data\stanford\postings.json"
 
#inference hyper-parameters
start_alpha=0.01
infer_epoch=1000
 

In [4]:

#load model
m = g.Doc2Vec.load(model)
#test_docs = [ x.strip().split() for x in codecs.open(test_docs, "r", "utf-8").readlines() ]



In [4]:

test_docs = pd.read_json(test_docs)
 
test_docs.head()

commentthreadid  Opinion  Question  Answer Sentiment Confusion  \
0               5,26331E+23        1         0       1         4         4   
1               5,26331E+23        0         1       1         4         4   
2               5,26331E+23        1         0       0         3         4   
3               5,30483E+23        0         0       0         5         4   
4  51b513008e8d330d00000001        0         1       0       3,5         4   

  Urgency                                               Text  \
0       3  [second, review, Although, applied, comments, ...   
1     4,5  [Also, got, Are, going, resubmit, see, get, be...   
2     5,5  [think, system, fair, reviewers, rush, process...   
3       2  [Thanks, It, useful, think, answers, Corey, ge...   
4       5  [Hello, Kristin, Thank, nice, usefull, Mooc, U...   

                forumpostid  CourseType  \
0  526563a587050a90ef000006    Medicine   
1  5264e2152cc6095e83000015    Medicine   
2  5263a0de9ec9282178000010    Medicine   
3               5,30483E+23  Humanities   
4  53e1dfb0fac7aaea13000007    Medicine   

                                   coursedisplayname  
0                         Medicine/SciWrite/Fall2013  
1                         Medicine/SciWrite/Fall2013  
2                         Medicine/SciWrite/Fall2013  
3  HumanitiesSciences/EP101/Environmental_Physiology  
4             Medicine/HRP258/Statistics_in_Medicine

In [5]:
test_docs['Opinion'].sum()

16463

In [6]:
test_docs['Opinion'].count()

29585

In [12]:

X=[]
for d in test_docs.Text:
     
    X.append( m.infer_vector(d, alpha=start_alpha, steps=infer_epoch) )

In [13]:
X

[array([-0.24878523,  0.05723966, -0.3036929 , -0.02731124,  0.27486506,
        -0.592805  ,  0.49763113,  0.15110739, -0.17546327,  0.30501264,
        -0.39378753, -0.09003238,  0.00510848,  0.18284197,  0.18161215,
         0.02077545, -0.26443642, -0.338952  , -0.044114  , -0.29912534,
        -0.02536505, -0.23981138,  0.3869224 , -0.20864004,  0.2736702 ,
         0.2715315 , -0.05569243, -0.24408303, -0.42294884, -0.8860087 ,
        -0.40458393,  0.17430855, -0.4721018 ,  0.12872672,  0.17373715,
        -0.01193386,  0.07358537, -0.21667099,  0.3007845 , -0.26854542,
         0.01450088,  0.4243774 , -0.15288593,  0.14056265,  0.31904218,
         0.11995348,  0.37964034, -0.30041015,  0.5714887 ,  0.28169793,
        -0.07068161,  0.04081354, -0.11648923, -0.07670406,  0.2610989 ,
         0.04234845,  0.1779883 ,  0.01667208, -0.02284713, -0.40149838,
         0.18129031, -0.33127978, -0.44437742, -0.44313076, -0.08071014,
        -0.0186365 , -0.5544457 , -0.9223115 ,  0.3

In [14]:
test_docs['Vector'] = X

In [15]:
test_docs.head()

commentthreadid  Opinion  Question  Answer Sentiment Confusion  \
0               5,26331E+23        1         0       1         4         4   
1               5,26331E+23        0         1       1         4         4   
2               5,26331E+23        1         0       0         3         4   
3               5,30483E+23        0         0       0         5         4   
4  51b513008e8d330d00000001        0         1       0       3,5         4   

  Urgency                                               Text  \
0       3  [second, review, Although, applied, comments, ...   
1     4,5  [Also, got, Are, going, resubmit, see, get, be...   
2     5,5  [think, system, fair, reviewers, rush, process...   
3       2  [Thanks, It, useful, think, answers, Corey, ge...   
4       5  [Hello, Kristin, Thank, nice, usefull, Mooc, U...   

                forumpostid  CourseType  \
0  526563a587050a90ef000006    Medicine   
1  5264e2152cc6095e83000015    Medicine   
2  5263a0de9ec9282178000010    Medicine   
3               5,30483E+23  Humanities   
4  53e1dfb0fac7aaea13000007    Medicine   

                                   coursedisplayname  \
0                         Medicine/SciWrite/Fall2013   
1                         Medicine/SciWrite/Fall2013   
2                         Medicine/SciWrite/Fall2013   
3  HumanitiesSciences/EP101/Environmental_Physiology   
4             Medicine/HRP258/Statistics_in_Medicine   

                                              Vector  
0  [-0.24878523, 0.05723966, -0.3036929, -0.02731...  
1  [-0.120419644, -0.079783045, -0.10196015, -0.3...  
2  [-0.8818892, 0.5847141, 0.049161777, -0.490729...  
3  [-0.16384728, 0.16297601, -0.21776049, -0.2263...  
4  [-0.20426929, 0.20647402, -0.3019723, 0.045810...

In [20]:
#carregando os dados
test_docs.reset_index().to_json(r'..\data\stanford\posting_vectors.json')

In [ ]:
#procedendo a vetorização a partir da base dad dados pré-treinada 
 
k=3
 
from sklearn.cluster import Birch
 
brc = Birch(branching_factor=50, n_clusters=k, threshold=0.1, compute_labels=True)
brc.fit(X)
 
clusters = brc.predict(X)
 
labels = brc.labels_
 
 
print ("Clusters: ")
print (clusters)
 
 
silhouette_score = metrics.silhouette_score(X, labels, metric='euclidean')
 
print ("Silhouette_score: ")
print (silhouette_score)
 
"""
Clusters: 
[1 0 0 1 1 2 1 0 1 1]
Silhouette_score: 
0.17644188
"""